This notebook uses the Dept. Ag, Water and the Environment's data on Species of National Environmental Significance
See https://environment.gov.au/science/erin/databases-maps/snes
and http://www.environment.gov.au/fed/catalog/search/resource/details.page?uuid=%7B337B05B6-254E-47AD-A701-C55D9A0435EA%7D

Specifically a subset of the "critically endangered" mammals listed in the dataset - Leadbetter Possum

# Install requisite software libraries

In [1]:
!pip install --quiet git+https://github.com/CSIRO-enviro-informatics/AusPIX_DGGS.git

In [11]:
!pip install --quiet geojson pygeoj matplotlib

Load the "critically_endangered_mammals_leadbetter.geojson" data file

In [12]:
import geojson 
import matplotlib
fname = "critically_endangered_mammals_leadbetter.geojson"
geojson_data = None
with open(fname) as json_file:
    geojson_data = geojson.load(json_file)
    

Show the locations of critically endangered leadbetter possums on a map

In [13]:
#draw the geometry for the feature on a map
import ipyleaflet as ipy 
import ipywidgets as ipyw
from ipyleaflet import GeoJSON, Map, Marker

x_coord = -37.8
y_coord = 145.89

map1 = ipy.Map(center=[x_coord, y_coord], zoom=8)
label = ipyw.Label(layout=ipyw.Layout(width='100%'))

geo_json1 = GeoJSON(data=geojson_data, style = {'color': 'red', 'opacity':0.8, 'weight':1.9, 'fillOpacity':0.5})
map1.add_layer(geo_json1)


In [14]:
## Critically endangered mammals: leadbetter Possum
map1

Map(center=[-37.8, 145.89], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [15]:
from pandas import json_normalize
features = geojson_data['features']
json_normalize(features)

type geometry.type                               geometry.coordinates  \
0  Feature  MultiPolygon  [[[[145.51, -37.82], [145.51, -37.83], [145.52...   
1  Feature  MultiPolygon  [[[[145.55, -37.89], [145.55, -37.92], [145.52...   

   properties.OBJECTID  properties.Shape_Leng  properties.Shape_Area  \
0                  173                   8.04                 0.1937   
1                  174                  13.68                 0.2404   

  properties.listed_id properties.map_id        properties.sci_name  \
0                  273               273  Gymnobelideus leadbeateri   
1                  273               273  Gymnobelideus leadbeateri   

  properties.comm_name  ... properties.tax_family properties.tax_order  \
0  Leadbeater's Possum  ...            Petauridae         Diprotodonta   
1  Leadbeater's Possum  ...            Petauridae         Diprotodonta   

  properties.tax_class properties.tax_phylum properties.tax_king  \
0             Mammalia              Chordata            Animalia   
1             Mammalia              Chordata            Animalia   

  properties.other_ids properties.cell_size properties.regions  \
0                 None                 0.01                VIC   
1                 None                 0.01                VIC   

                               properties.attributio  \
0  Species 1km Grids August 2019 Canberra: Depart...   
1  Species 1km Grids August 2019 Canberra: Depart...   

                               properties.sprat_prof  
0  http://www.environment.gov.au/cgi-bin/sprat/pu...  
1  http://www.environment.gov.au/cgi-bin/sprat/pu...  

[2 rows x 26 columns]

In [16]:
from auspixdggs.callablemodules.dggs_in_poly_for_geojson_callable import cells_in_poly
from auspixdggs.callablemodules.dggs_in_line import line_to_DGGS, densify_my_line
import geojson
from geojson.utils import coords
from shapely.geometry import shape, LineString, MultiLineString, Polygon, MultiPolygon

def get_geojson_by_file(fname):
    data = None
    with open(fname) as json_file:
        data = geojson.load(json_file)
    return data

def geojson_to_shape(g):
    return shape(g)
    
def bbox(coord_list):
     box = []
     for i in (0,1):
         res = sorted(coord_list, key=lambda x:x[i])
         box.append((res[0][i],res[-1][i]))
     #ret = f"({box[0][0]} {box[1][0]}, {box[0][1]} {box[1][1]})"
     ret = [ box[0][0], box[1][0], box[0][1], box[1][1] ]
     #print("BBOX {}".format(ret))
     return ret

def get_cells_in_geojson(geojson, resolution, cell_obj=True):
    list_cells = []
    #print("Type geojson: {}".format(type(geojson)))
    dict_cells = {}
    for fea in geojson['features']:  # for feature in attribute table
        #print(fea)
        res_cells = get_cells_in_feature(fea, resolution, cell_obj=cell_obj)
        print(res_cells)
        for item in res_cells:
            print("'{}'".format(str(item)))
        #cell_list = [item[0] for item in res_cells]
        cell_list = res_cells
        #cell_id_list = res_cells
        for cell in cell_list:
            cell_id = str(cell)
            if cell_id not in dict_cells:
                dict_cells[cell_id] = cell
    list_cells = list(dict_cells.values())
    return list_cells 

def get_cells_in_feature(fea, resolution, cell_obj=True):
    geom = geojson_to_shape(fea['geometry'])
    curr_coords = list(coords(fea))
    thisbbox = bbox(curr_coords)
    cells = []
    if isinstance(geom, LineString) or isinstance(geom, MultiLineString): 
        fea['geometry']['coordinates'] = densify_my_line(fea['geometry']['coordinates'], resolution)
        curr_coords = list(coords(fea))
        print(curr_coords)        
        res_cells = line_to_DGGS(curr_coords, resolution)  # start at DGGS level 10   
        cells = [str(item) for item in res_cells]
    elif isinstance(geom, Polygon) or  isinstance(geom, MultiPolygon):
        res_cells = cells_in_poly(thisbbox, fea['geometry']['coordinates'], resolution, return_cell_obj=cell_obj)  # start at DGGS level 10    
        print(res_cells)
        cells = [item[0] for item in res_cells]
    else: #try something anyway
        res_cells = cells_in_poly(thisbbox, fea['geometry']['coordinates'], resolution, return_cell_obj=cell_obj)  # start at DGGS level 10    
        print(res_cells)
        cells = [item[0] for item in res_cells]
    return cells   

# Use the Geoscience Australia AusPIX DGGS Engine to DGGS-enable the data

Use the DGGS Engine to find cells that match the features. Also specify the DGGS resolution needed.

In [17]:
DGGS_RESOLUTION=7

In [18]:
%%time
list_cells = get_cells_in_geojson(geojson_data, DGGS_RESOLUTION, True)  

auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix


auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix
auspixengine.pj_rhealpix


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




'R7848086187'
'R7848086188'
'R7848086266'
'R7848086267'
'R7848086268'
'R7848086276'
'R7848086277'
'R7848086278'
'R7848086286'
'R7848086287'
'R7848086288'
'R7848087066'
'R7848087067'
'R7848087068'
'R7848087076'
'R7848087077'
'R7848087078'
'R7848087086'
'R7848087087'
'R7848087088'
'R7848087166'
'R7848087167'
'R7848087286'
'R7848087287'
'R7848087288'
'R7848088066'
'R7848088067'
'R7848088068'
'R7848088076'
'R7848088077'
'R7848088078'
'R7848088086'
'R7848088087'
'R7848088088'
'R7848088166'
'R7848088167'
'R7848088168'
'R7848088176'
'R7848088177'
'R7848088178'
'R7848088186'
'R7848088187'
'R7848088188'
'R7848088266'
'R7848088267'
'R7848088268'
'R7848088276'
'R7848088277'
'R7848088278'
'R7848088286'
'R7848088287'
'R7848088288'
'R7848166066'
'R7848166067'
'R7848166068'
'R7848166076'
'R7848166077'
'R7848166078'
'R7848166086'
'R7848166087'
'R7848166088'
'R7848086312'
'R7848086320'
'R7848086321'
'R7848086322'
'R7848086400'
'R7848086401'
'R7848086402'
'R7848086410'
'R7848086411'
'R7848086412'
'R784

'R7848087636'
'R7848087637'
'R7848087638'
'R7848087646'
'R7848087647'
'R7848087648'
'R7848087656'
'R7848087657'
'R7848087658'
'R7848087736'
'R7848087737'
'R7848087738'
'R7848087746'
'R7848087747'
'R7848087748'
'R7848087756'
'R7848087757'
'R7848087758'
'R7848087836'
'R7848087837'
'R7848087838'
'R7848087846'
'R7848087847'
'R7848087848'
'R7848087856'
'R7848087857'
'R7848087858'
'R7848088636'
'R7848088637'
'R7848088638'
'R7848088646'
'R7848088647'
'R7848088648'
'R7848088656'
'R7848088657'
'R7848088658'
'R7848088736'
'R7848088737'
'R7848088738'
'R7848088746'
'R7848088747'
'R7848088748'
'R7848088756'
'R7848088757'
'R7848088758'
'R7848088836'
'R7848088837'
'R7848088838'
'R7848088846'
'R7848088847'
'R7848088848'
'R7848088856'
'R7848088857'
'R7848088858'
'R7848166636'
'R7848166637'
'R7848166638'
'R7848166646'
'R7848166647'
'R7848166648'
'R7848166656'
'R7848166657'
'R7848166658'
'R7848166736'
'R7848166737'
'R7848166738'
'R7848166746'
'R7848166747'
'R7848166748'
'R7848166756'
'R7848086860'
'R7848

...

'R7848754277'
'R7848754278'
'R7848754286'
'R7848754287'
'R7848754288'
'R7848755066'
'R7848755067'
'R7848755068'
'R7848755278'
'R7848755286'
'R7848755287'
'R7848755288'
'R7848833066'
'R7848833067'
'R7848833068'
'R7848833076'
'R7848833077'
'R7848833078'
'R7848833086'
'R7848833087'
'R7848833088'
'R7848833166'
'R7848833167'
'R7848833168'
'R7848833176'
'R7848833177'
'R7848833178'
'R7848833186'
'R7848833187'
'R7848833188'
'R7848833266'
'R7848833267'
'R7848833268'
'R7848833276'
'R7848833277'
'R7848833278'
'R7848833286'
'R7848833287'
'R7848833288'
'R7848834066'
'R7848834067'
'R7848834068'
'R7848834076'
'R7848834077'
'R7848834078'
'R7848834086'
'R7848834087'
'R7848834088'
'R7848834166'
'R7848834167'
'R7848834168'
'R7848834176'
'R7848834177'
'R7848834178'
'R7848834186'
'R7848834187'
'R7848834188'
'R7848834266'
'R7848834267'
'R7848834268'
'R7848644411'
'R7848644412'
'R7848644420'
'R7848644421'
'R7848644422'
'R7848644500'
'R7848644501'
'R7848644502'
'R7848644510'
'R7848644511'
'R7848644512'
'R7848

'R7848653487'
'R7848653488'
'R7848653566'
'R7848653567'
'R7848653568'
'R7848653576'
'R7848653577'
'R7848653578'
'R7848653586'
'R7848653587'
'R7848653588'
'R7848654366'
'R7848654367'
'R7848654368'
'R7848654376'
'R7848654377'
'R7848654378'
'R7848654386'
'R7848654387'
'R7848654388'
'R7848654466'
'R7848654467'
'R7848654468'
'R7848654476'
'R7848654477'
'R7848654478'
'R7848654486'
'R7848654487'
'R7848654488'
'R7848654566'
'R7848654567'
'R7848654568'
'R7848654576'
'R7848654577'
'R7848654578'
'R7848654586'
'R7848654587'
'R7848654588'
'R7848655366'
'R7848655367'
'R7848655368'
'R7848655376'
'R7848655377'
'R7848655378'
'R7848655386'
'R7848655387'
'R7848655388'
'R7848655466'
'R7848655467'
'R7848655468'
'R7848655476'
'R7848655477'
'R7848655478'
'R7848655486'
'R7848655487'
'R7848655488'
'R7848655566'
'R7848655567'
'R7848655568'
'R7848655576'
'R7848655577'
'R7848655578'
'R7848655586'
'R7848655587'
'R7848655588'
'R7848733366'
'R7848733367'
'R7848733368'
'R7848733376'
'R7848733377'
'R7848733378'
'R7848

'R7848655671'
'R7848655672'
'R7848655680'
'R7848655681'
'R7848655682'
'R7848655760'
'R7848655761'
'R7848655762'
'R7848655770'
'R7848655771'
'R7848655772'
'R7848655780'
'R7848655781'
'R7848655782'
'R7848655860'
'R7848655861'
'R7848655862'
'R7848655870'
'R7848655871'
'R7848655872'
'R7848655880'
'R7848655881'
'R7848655882'
'R7848733660'
'R7848733661'
'R7848733662'
'R7848733670'
'R7848733671'
'R7848733672'
'R7848733680'
'R7848733681'
'R7848733682'
'R7848733760'
'R7848733761'
'R7848733762'
'R7848733770'
'R7848733771'
'R7848733772'
'R7848733780'
'R7848733781'
'R7848733782'
'R7848733860'
'R7848733861'
'R7848733862'
'R7848733870'
'R7848733871'
'R7848733872'
'R7848733880'
'R7848733881'
'R7848733882'
'R7848734660'
'R7848734661'
'R7848734662'
'R7848734670'
'R7848734671'
'R7848734672'
'R7848734680'
'R7848734681'
'R7848734682'
'R7848734760'
'R7848734761'
'R7848734762'
'R7848734770'
'R7848734771'
'R7848734772'
'R7848734780'
'R7848734781'
'R7848734782'
'R7848734860'
'R7848734861'
'R7848734862'
'R7848

'R7848736173'
'R7848736174'
'R7848736175'
'R7848736183'
'R7848736184'
'R7848736185'
'R7848736263'
'R7848736264'
'R7848736265'
'R7848736273'
'R7848737085'
'R7848737163'
'R7848737164'
'R7848737165'
'R7848737173'
'R7848737174'
'R7848737175'
'R7848737183'
'R7848737184'
'R7848737185'
'R7848737263'
'R7848737264'
'R7848737265'
'R7848737273'
'R7848737274'
'R7848737275'
'R7848737283'
'R7848737284'
'R7848737285'
'R7848738063'
'R7848648287'
'R7848648288'
'R7848656066'
'R7848656067'
'R7848656068'
'R7848656076'
'R7848656077'
'R7848656078'
'R7848656086'
'R7848656087'
'R7848656088'
'R7848656166'
'R7848656167'
'R7848656168'
'R7848656176'
'R7848656177'
'R7848656178'
'R7848656186'
'R7848656187'
'R7848656188'
'R7848656266'
'R7848656267'
'R7848656268'
'R7848656276'
'R7848656277'
'R7848656278'
'R7848656286'
'R7848656287'
'R7848656288'
'R7848657066'
'R7848657067'
'R7848657068'
'R7848657076'
'R7848657077'
'R7848657078'
'R7848657086'
'R7848657087'
'R7848657088'
'R7848657166'
'R7848657167'
'R7848657168'
'R7848

CPU times: user 9min 39s, sys: 1.44 s, total: 9min 41s
Wall time: 9min 48s


In [10]:
from auspixdggs.callablemodules.dggs_in_poly_for_geojson_callable import cells_in_poly, get_dggs_cell_bbox
from geojson import Feature, FeatureCollection

list_features = []
for cell in list_cells:
    bbox_coords = get_dggs_cell_bbox(cell)
    geom_obj = Polygon(bbox_coords)
    feat = Feature(geometry=geom_obj, properties={"dggs_cell_id": str(cell)}) 
    list_features.append(feat)

feature_collection = FeatureCollection(list_features)

Show the matching DGGS Cells on a map

In [11]:
map2 = ipy.Map(center=[x_coord, y_coord], zoom=9)
label = ipyw.Label(layout=ipyw.Layout(width='100%'))

geo_json2 = GeoJSON(data=feature_collection, 
                    style={
                          'color': 'black', 
                          'opacity': 1, 
                          'weight':1, 
                          'fillColor': 'blue', 
                          'fillOpacity': 0.2})
map2.add_layer(geo_json1)
map2.add_layer(geo_json2)



In [12]:
# DGGS Enabled version - Critically endangered mammals: leadbetter Possum

map2


Map(center=[-37.8, 145.89], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

# Query the Loc-I Integration API for matching LGAs

In [13]:
import requests
import json
#iterate over features in feature collection and query Loc-I API for features
def find_features_at_dggs_cell(dggs_cell_id):
    payload = {
        'dggs_cell' : dggs_cell_id
    }
    r = requests.get('https://api.loci.cat/api/v1/location/find-at-DGGS-cell', params=payload)
    json_res = r.json()
    return json_res


In [25]:
target_feature_type = 'asgs16_lga'

set_of_lga_features = set([])
#print(feature_collection)
for feature in feature_collection['features']:
    cell_id = feature['properties']['dggs_cell_id']
    #pad it out
    cell_id = cell_id + "444"
    print("Processing {}".format(cell_id))
    res = find_features_at_dggs_cell(cell_id)
    if 'locations' in res:
        for loc in res['locations']:
            if 'dataType' in loc and loc['dataType'] == target_feature_type:
                set_of_lga_features.add(loc['uri'])
                print("Adding {}".format(loc['uri']))

    


Processing R7848085444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848086444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848087444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848088444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848166444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848321444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848322444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848400444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7847525444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing R7848403444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/25620
Processing

Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848704444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848713444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848714444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848723444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848724444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848725444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848803444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848804444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848805444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848616444
Adding htt

Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/27450
Processing R7848446444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/27450
Processing R7848447444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/27450
Processing R7848448444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848456444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848457444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848458444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/20830
Processing R7848360444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/27450
Processing R7848361444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/27450
Processing R7848380444
Adding http://linked.data.gov.au/dataset/asgs2016/localgovernmentarea/27450
Processing R7848381444
Adding htt

In [26]:
def get_geom(loci_uri):
    payload = {
        "uri": loci_uri
    }
    url = "https://api.loci.cat/api/v1/location/geometry"
    r = requests.get(url, params=payload)
    res = r.json()
    #get the first geom result
    geojson_data = []
    if len( res['geometry']) > 0:
        geojson_data = res['geometry'][0]
    return geojson_data



Show the matching LGAs on a map

In [27]:
map3 = ipy.Map(center=[x_coord, y_coord], zoom=7)
label = ipyw.Label(layout=ipyw.Layout(width='100%'))


In [28]:
for feature_uri in list(set_of_lga_features):
    geojson_data = get_geom(feature_uri)
    curr_geojson_layer = GeoJSON(data=geojson_data, 
                    style={
                          'color': 'black', 
                          'opacity': 1, 
                          'weight':1, 
                          'fillColor': 'yellow', 
                          'fillOpacity': 0.3})
    map3.add_layer(curr_geojson_layer)
map3.add_layer(geo_json1)
map3.add_layer(geo_json2)


In [29]:
map3

Map(center=[-37.8, 145.89], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

# Try a different Loc-I Feature - Query the Loc-I Integration API for matching ASGS Statistical Area Level 2 locations

In [19]:
target_feature_type = 'asgs16_sa2'

set_of_features = set([])
#print(feature_collection)
for feature in feature_collection['features']:
    cell_id = feature['properties']['dggs_cell_id']
    #pad it out
    cell_id = cell_id + "000"
    print("Processing {}".format(cell_id))
    res = find_features_at_dggs_cell(cell_id)
    if 'locations' in res:
        for loc in res['locations']:
            if 'dataType' in loc and loc['dataType'] == target_feature_type:
                set_of_features.add(loc['uri'])
                print("Adding {}".format(loc['uri']))


Processing R7848085000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848086000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848087000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848088000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848166000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848321000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848322000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7848400000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011054
Processing R7847525000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011062
Processing R7848403000
Adding http://linked.data.gov.au

Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051285
Processing R7848614000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051286
Processing R7848615000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051286
Processing R7848623000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051286
Processing R7848624000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011077
Processing R7848625000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011077
Processing R7848703000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011077
Processing R7848704000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011077
Processing R7848713000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011077
Processing R7848714000
Adding http://linked.data.gov.au/dataset/asgs2016/stati

Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051276
Processing R7848337000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051276
Processing R7848338000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051276
Processing R7848347000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/211051286
Processing R7848348000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011061
Processing R7848356000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011061
Processing R7848357000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011061
Processing R7848358000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011061
Processing R7848436000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/204011061
Processing R7848438000
Adding http://linked.data.gov.au/dataset/asgs2016/stati

Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011076
Processing R7848657000
Adding http://linked.data.gov.au/dataset/asgs2016/statisticalarealevel2/205011077


Show the matching ASGS SA2 on a map

In [20]:

map4 = ipy.Map(center=[x_coord, y_coord], zoom=8)


for feature_uri in list(set_of_features):
    geojson_data = get_geom(feature_uri)
    curr_geojson_layer = GeoJSON(data=geojson_data, 
                    style={
                          'color': 'black', 
                          'opacity': 1, 
                          'weight':1, 
                          'fillColor': 'green', 
                          'fillOpacity': 0.3})
    map4.add_layer(curr_geojson_layer)

    
map4.add_layer(geo_json1)
map4.add_layer(geo_json2)

In [21]:
map4

Map(center=[-37.8, 145.89], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

# Try a different Loc-I Feature-type again - Query the Loc-I Integration API for matching ASGS State Suburbs

In [22]:
target_feature_type = 'asgs16_ssc'

set_of_features = set([])
#print(feature_collection)
for feature in feature_collection['features']:
    cell_id = feature['properties']['dggs_cell_id']
    #pad it out
    cell_id = cell_id + "000"
    print("Processing {}".format(cell_id))
    res = find_features_at_dggs_cell(cell_id)
    if 'locations' in res:
        for loc in res['locations']:
            if 'dataType' in loc and loc['dataType'] == target_feature_type:
                set_of_features.add(loc['uri'])
                print("Adding {}".format(loc['uri']))


Processing R7848085000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22198
Processing R7848086000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22198
Processing R7848087000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22198
Processing R7848088000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22198
Processing R7848166000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20844
Processing R7848321000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22198
Processing R7848322000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22198
Processing R7848400000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20844
Processing R7847525000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/21013
Processing R7848403000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20844
Processing R7847526000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22523

Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20166
Processing R7848803000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20166
Processing R7848804000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20166
Processing R7848805000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22493
Processing R7848616000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22501
Processing R7848617000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20988
Processing R7848618000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22103
Processing R7848626000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22103
Processing R7848627000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20006
Processing R7848628000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20006
Processing R7848706000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/21942
Processing R7848727000

Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20450
Processing R7848482000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/21257
Processing R7848363000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/21802
Processing R7848383000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20827
Processing R7848384000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/21620
Processing R7848385000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22147
Processing R7848463000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22147
Processing R7848464000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/22147
Processing R7848465000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20450
Processing R7848473000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/20450
Processing R7848483000
Adding http://linked.data.gov.au/dataset/asgs2016/statesuburb/21257
Processing R7848485000

Show the matching State Suburbs on a map

In [23]:

map5 = ipy.Map(center=[x_coord, y_coord], zoom=8)


for feature_uri in list(set_of_features):
    geojson_data = get_geom(feature_uri)
    curr_geojson_layer = GeoJSON(data=geojson_data, 
                    style={
                          'color': 'black', 
                          'opacity': 1, 
                          'weight':1, 
                          'fillColor': 'purple', 
                          'fillOpacity': 0.3})
    map5.add_layer(curr_geojson_layer)

    
map5.add_layer(geo_json1)
map5.add_layer(geo_json2)

In [24]:
map5

Map(center=[-37.8, 145.89], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…